# 0. PASOS PREVIOS

## 0.1 Librerías

In [1]:
%time
import io
import pandas as pd
import numpy as np
from datetime import date
import matplotlib.pyplot as plt
import seaborn as sn
import json
from IPython.display import Image
import cufflinks as cf
from IPython.display import display,HTML
import seaborn as sns
import plotly.express as px
import time
from datetime import time

CPU times: user 1e+03 ns, sys: 0 ns, total: 1e+03 ns
Wall time: 3.1 µs


## 0.2  Funciones y otro Código a importar

In [2]:
def analisis_DF(x):
    a = x.shape
    b = x.size
    c = x.ndim
    d = x.info()
    return f"{a} filas por culumna, {b} total datos, {c} num. dimensiones. \n Estructura: \n {d}" 

def analisis_DF_2(x):
    a = print("INDICES: \n",x.index,"\n")
    b = print("COLUMNAS: \n",x.columns,"\n")
    c = print("VALORES: \n",x.values,"\n)")

def media_grupo(x):
    x = stats_grupo(x).drop(["count","25%","50%","75%","std","min","max"], axis=0)
    return x

def quitar_lista_columna (DF, col): ### Importante: introducir con como str "col"
    df_sin_lista = DF[col].apply(lambda x: x[0] if len(x) > 0 else x)
    df_sin_lista = df_sin_lista.to_frame()
    return df_sin_lista

def quitar_diccionario_primario (DF, col): ### Importante: introducir con como str "col"
    resultado = DF[col].apply(lambda x : x.get("reaction"))
    resultado = resultado.to_frame()
    return resultado

def descomprimir_diccionario (DF, col): ### Importante: introducir con como str "col"
    resultado = DF[col].apply(pd.Series)
    return resultado

def atributos_fechas(x):
    x['año'] = x.index.year
    x['mes'] = x.index.month_name()
    x['dia_mes'] = x.index.day
    x['dia_semana'] = x.index.day_name()
    x['hora'] = x.index.hour
    return(x)

def fechas_a_numeros(df,colsemana,colmes):
    df[colsemana].replace({"Monday": 1,
                                 "Tuesday": 2,
                                 "Wednesday": 3,
                                 "Thursday": 4,
                                 "Friday": 5,
                                 "Saturday": 6,
                                 "Sunday": 7}, inplace= True) 
    df[colmes].replace({"January": 1,
                              "February": 2,
                              "March": 3,
                              "April": 4,
                              "May": 5,
                              "June": 6,
                              "July": 7,
                             "August": 8,
                             "September": 9,
                             "October": 10,
                              "November": 11,
                               "December": 12}, inplace = True)  
    return df

## 0.3. Definición de Objetivos

1. Carga de datos eficiente.
2. Definición de funciones de extracción y limpieza de datos.
3. Obtención de nuevas variables.
4. Visualización efectiva de la información.
5. Describir las principales tendencias de likes y reactions del usuario.
6. Exposición clara y concisa de principales insights y hallazgos.

## 0.4. Observaciones

1. La información de las bases de datos utilizadas cubren solo hasta 2016, lo que posiblemenete sea debido a la entrada del RGPD (REGLAMENTO (UE) 2016/679 DEL PARLAMENTO EUROPEO Y DEL CONSEJO de 27 de abril de 2016 relativo a la protección de las personas físicas en lo que respecta al tratamiento de datos personales y a la libre circulación de estos datos y por el que se deroga la Directiva 95/46/CE (Reglamento general de protección de datos).

2. Los datos empleados en este ejemplo corresponden con los de un estudiante de edad media.


# 1. CARGA DE DATOS

## 1.1. Likes y Reacciones

In [3]:
%time
dfl0 = pd.read_json("likes_and_reactions_1.json")
dfl1 = pd.read_json("likes_and_reactions_2.json")
dfl2 = pd.read_json("likes_and_reactions_2.json")


CPU times: user 1 µs, sys: 0 ns, total: 1 µs
Wall time: 2.86 µs


# 2. ANÁLISIS EXPLORATORIO

In [4]:
# %time
df_likes = pd.concat([dfl0, dfl1, dfl2], axis=0)
df_likes.head(5)

timestamp                                               data  \
0 2010-07-07 10:15:10  [{'reaction': {'reaction': 'LIKE', 'actor': 'L...   
1 2010-07-14 17:03:35  [{'reaction': {'reaction': 'LIKE', 'actor': 'L...   
2 2010-09-07 18:07:58  [{'reaction': {'reaction': 'LIKE', 'actor': 'L...   
3 2010-09-09 10:19:29  [{'reaction': {'reaction': 'LIKE', 'actor': 'L...   
4 2010-09-12 08:05:45  [{'reaction': {'reaction': 'LIKE', 'actor': 'L...   

                                               title  
0  A Lucas Vivo le ha gustado el enlace de Anonym...  
1  A Lucas Vivo le ha gustado el enlace de Anonym...  
2  A Lucas Vivo le ha gustado el enlace de Hattor...  
3  A Lucas Vivo le ha gustado el enlace de Anonym...  
4  A Lucas Vivo le ha gustado el enlace de Jorge ...

Dado que solo conteiene información redundante, vamos a eliminar la columna Title

In [5]:
df_likes = df_likes.drop(columns = "title")

In [6]:
analisis_DF(df_likes)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 7500 entries, 0 to 2499
Data columns (total 2 columns):
 #   Column     Non-Null Count  Dtype         
---  ------     --------------  -----         
 0   timestamp  7500 non-null   datetime64[ns]
 1   data       7500 non-null   object        
dtypes: datetime64[ns](1), object(1)
memory usage: 175.8+ KB


'(7500, 2) filas por culumna, 15000 total datos, 2 num. dimensiones. \n Estructura: \n None'

In [7]:
analisis_DF_2(df_likes)

INDICES: 
 Int64Index([   0,    1,    2,    3,    4,    5,    6,    7,    8,    9,
            ...
            2490, 2491, 2492, 2493, 2494, 2495, 2496, 2497, 2498, 2499],
           dtype='int64', length=7500) 

COLUMNAS: 
 Index(['timestamp', 'data'], dtype='object') 

VALORES: 
 [[Timestamp('2010-07-07 10:15:10')
  list([{'reaction': {'reaction': 'LIKE', 'actor': 'Lucas Vivo'}}])]
 [Timestamp('2010-07-14 17:03:35')
  list([{'reaction': {'reaction': 'LIKE', 'actor': 'Lucas Vivo'}}])]
 [Timestamp('2010-09-07 18:07:58')
  list([{'reaction': {'reaction': 'LIKE', 'actor': 'Lucas Vivo'}}])]
 ...
 [Timestamp('2016-04-17 19:56:51')
  list([{'reaction': {'reaction': 'HAHA', 'actor': 'Lucas Vivo'}}])]
 [Timestamp('2016-04-17 20:58:14')
  list([{'reaction': {'reaction': 'HAHA', 'actor': 'Lucas Vivo'}}])]
 [Timestamp('2016-04-18 06:28:55')
  list([{'reaction': {'reaction': 'LIKE', 'actor': 'Lucas Vivo'}}])]] 
)


## 2.1 Detección de nulos y duplicados

In [8]:
nulos = df_likes.isnull().sum()
nulos

timestamp    0
data         0
dtype: int64

In [9]:
#duplicados =df_likes.duplicated().sum() #se quita de la ejecución porque se detectan.
#duplicados

## 2.3 Conclusiones
Resulta necesario un trabajo previo de extracción de datos para la creación de nuevas variables.

# 3 . CREACIÓN DE NUEVAS VARIABLES

## 3.1  Likes y Reacciones 

De la columna de df_likes vamos a "desencapsular" la información  con una función lambda. También comprobaremos que la longitud del DF resultante coincide con el original.

Para ello el primer paso es eliminar la primera columna. Aplicaremos una función en vez de acudir a un bucle. (Esta función es cortesía de mi profe del bootcamp :))

In [10]:
def quitar_lista_columna (DF, col): ### Importante: introducir con como str "col"
    df_sin_lista = DF[col].apply(lambda x: x[0] if len(x) > 0 else x)
    df_sin_lista = df_sin_lista.to_frame()
    return df_sin_lista

In [11]:
df_likes1 = quitar_lista_columna(df_likes,"data")

In [12]:
len(df_likes1) == len(df_likes)

True

El siguiente paso es pasar los diccionarios a columnas, para ello eliminamos el "diccionario externo" de cada columna. 

In [13]:
def quitar_diccionario_primario (DF, col): ### Importante: introducir con como str "col"
    resultado = DF[col].apply(lambda x : x.get("reaction"))
    resultado = resultado.to_frame()
    return resultado


In [14]:
df_likes2 = quitar_diccionario_primario(df_likes1,"data")

In [15]:
def descomprimir_diccionario (DF, col): ### Importante: introducir con como str "col"
    resultado = DF[col].apply(pd.Series)
    return resultado

In [16]:
df_likes3 = descomprimir_diccionario(df_likes2, "data")
df_likes3

reaction       actor
0        LIKE  Lucas Vivo
1        LIKE  Lucas Vivo
2        LIKE  Lucas Vivo
3        LIKE  Lucas Vivo
4        LIKE  Lucas Vivo
...       ...         ...
2495     LIKE  Lucas Vivo
2496     LIKE  Lucas Vivo
2497     HAHA  Lucas Vivo
2498     HAHA  Lucas Vivo
2499     LIKE  Lucas Vivo

[7500 rows x 2 columns]

In [17]:
len(df_likes3) == len(df_likes2)

True

In [18]:
df_likes3 = df_likes3.reset_index()
df_likes3.rename({"Index":"level_0"}, axis=1)


index reaction       actor
0         0     LIKE  Lucas Vivo
1         1     LIKE  Lucas Vivo
2         2     LIKE  Lucas Vivo
3         3     LIKE  Lucas Vivo
4         4     LIKE  Lucas Vivo
...     ...      ...         ...
7495   2495     LIKE  Lucas Vivo
7496   2496     LIKE  Lucas Vivo
7497   2497     HAHA  Lucas Vivo
7498   2498     HAHA  Lucas Vivo
7499   2499     LIKE  Lucas Vivo

[7500 rows x 3 columns]

### Observación
Conviene señalar que se conserva el INDEX original como precaución ante los posteriores tratamientos de datos.

### 3.1.1.  Obtención de variables temporales

In [19]:
df_likes["timestamp"] = pd.to_datetime(df_likes["timestamp"])

También creamos un nuevo DF que almacene la fecha original y un contador.

In [20]:
df_likesT = df_likes

In [21]:
df_likesT["num"] = 1

Seguimos generando las fechas. 

In [22]:
df_likes_t = df_likes.reset_index()
df_likes_t = df_likes_t.set_index("timestamp")


In [23]:
df_likes_tiempo = atributos_fechas(df_likes_t)

De cara a optimizar la visualización y el análisis de datos, se procede a renombrar los días de la semana y meses con la siguiente función basada en replace:

In [24]:
df_likes_tiempo_def = fechas_a_numeros(df_likes_tiempo,"dia_semana","mes")

## 3.3 Creación DFs consolidados

Cabe reseñar que los DF de distintos grupos de información no pueden unirse, dado que tienen índices distintos. 

In [25]:
likes_DEF = pd.merge(left =df_likes3, right = df_likes_tiempo_def, on = "index", how = "outer" )

Ahora procedemos a eliminar las columnas inservibles con DROP.

In [26]:
likes_ = likes_DEF.drop(columns= ["index","actor","data"])

In [27]:
likes_T = likes_.groupby(["año","mes","hora"])["num"].count()
likes_T = likes_T.reset_index()

# 4 ANÁLISIS DE DATOS Y VISUALIZACIÓN

## 4.1 Por año y tipo

In [28]:
px.histogram(data_frame = likes_,
             x          = "año",
             hover_data = ["reaction"],
             color      = "reaction",
             nbins      = 20)

## 4.2 A lo largo del año

In [29]:
px.histogram(data_frame = likes_,
             x          = "mes",
             hover_data = ["reaction"],
             color      = "año",
            nbins = 23)

In [30]:
px.histogram(data_frame = likes_,
             x          = "mes", 
             hover_data = ["reaction"],
             color      = "reaction",
             marginal   = "rug",
             facet_col = "año")

## 4.3 A lo largo de la semana

In [31]:
px.histogram(data_frame = likes_,
             x          = "dia_semana",
             hover_data = ["reaction"],
             color      = "año",
            nbins = 23)

In [32]:
px.histogram(data_frame = likes_,
             x          = "dia_semana", 
             hover_data = ["reaction"],
             color      = "reaction",
             marginal   = "rug",
             facet_col = "año")

## 4.4 A lo largo del día

In [33]:
px.histogram(data_frame = likes_,
             x          = "hora",
             hover_data = ["reaction"],
             color      = "año",
            nbins = 47)

In [34]:
px.histogram(data_frame = likes_,
             x          = "hora", 
             hover_data = ["reaction"],
             color      = "reaction",
             marginal   = "rug",
             facet_col = "año")

In [35]:
px.histogram(data_frame = likes_T,
             x          = "hora",
             y = "num",
             hover_data = ["num"],
             color      = "año",
            nbins = 50)

In [36]:
likes_T2 = likes_.groupby(["año","mes","dia_semana","hora"])["num"].count()
likes_T2 = likes_T2.reset_index()


In [37]:
px.histogram(data_frame = likes_T2,
             x          = "hora", 
             hover_data = ["num"],
             color      = "año",
             marginal   = "rug",
             facet_row = "dia_semana")

# 5. CONCLUSIONES

Tras la exploración realizada se extraen las siguientes conclusiones:

1. No hay un uso suficiente de las reacciones distintas a LIKE para extraer conclusiones respecto a esta variable categórica.

2. El nivel de actividad varía entre los años, pero siguen un patrón muy similar en la distribucióna a lo largo del año, meses, y horario.

3. Los días de la semana de mayor actividad son el Domingo, Sábado, y Lunes.

4. Los meses de menor actividad son los de verano.

5. Las horas de mayor actividad son entre las 21 y las 24 horas.